Data Preprocess

In [3]:
import pandas as pd
import os

# Define the file path and sheet names
file_path = 'Assignment 2 GHGHighlights Data.XLS'
sheets = ['GHG Energy', 'GHG Fugi', 'CO2 MARBUNK', 'CO2 AVBUNK', 'CO2-TES', 'CO2-GDP', 'CO2-GDP PPP', 'CO2-POP',
          'GHG FC', 'GHG FC - Coal', 'GHG FC - Oil', 'GHG FC - Gas']
years_range = range(1971, 2022)
regions_to_exclude = ["OECD Americas", "OECD Asia Oceania", "OECD Europe",
                      "Non-OECD Europe and Eurasia", "Africa", "Asia (excl. China)",
                      "China (incl. Hong Kong, China)", "Non-OECD Americas", "Middle East"]

# Create a directory for output if it doesn't exist
if not os.path.exists('data'):
    os.makedirs('data')

# Process each year
for year in years_range:
    year_data = pd.DataFrame()

    # Process each sheet
    for sheet in sheets:
        if sheet in ['GHG FC', 'GHG FC - Coal', 'GHG FC - Oil', 'GHG FC - Gas']:
            start_row, end_row = 23, 187  # Rows start at 24 and end at 188 for these sheets
        else:
            start_row, end_row = 21, 185  # Rows start at 22 and end at 186 for original sheets

        # Load data from Excel
        data = pd.read_excel(file_path, sheet_name=sheet, skiprows=start_row, nrows=end_row - start_row, usecols="A:AZ",
                             engine='xlrd')
        specific_year_data = data.filter(regex=str(year))
        countries = data['Region/Country/Economy']
        mask = ~countries.isin(regions_to_exclude)
        specific_year_data = specific_year_data[mask]
        countries = countries[mask]
        country_data = pd.DataFrame(specific_year_data.values, index=countries, columns=[sheet])
        year_data = pd.concat([year_data, country_data], axis=1)

    # Save the processed data to a CSV file
    year_data.to_csv(f'data/{year}.csv', encoding='utf-8')


Task 3 

In [4]:
import pandas as pd
import numpy as np
from minisom import MiniSom
from sklearn.preprocessing import StandardScaler
import plotly.graph_objects as go

# Prepare combined dataset
file_paths = [f'data/{year}.csv' for year in range(1971, 2022)]
data_list = []

for file_path in file_paths:
    year_data = pd.read_csv(file_path)
    year_data['Year'] = file_path.split('/')[-1].split('.')[0]
    data_list.append(year_data)

# Concatenate all years data
data = pd.concat(data_list, ignore_index=True)

# Select relevant columns for clustering and handle missing data
selected_columns = [
    'Region/Country/Economy', 'GHG Energy', 'GHG Fugi', 'CO2 MARBUNK', 'CO2 AVBUNK', 
    'CO2-TES', 'CO2-GDP', 'CO2-GDP PPP', 'CO2-POP', 'GHG FC', 'GHG FC - Coal', 
    'GHG FC - Oil', 'GHG FC - Gas'
]
data = data[['Year'] + selected_columns]
data.replace(['..', np.nan], 0, inplace=True)
data[selected_columns[1:]] = data[selected_columns[1:]].apply(pd.to_numeric, errors='coerce')

# Normalize features and calculate SOM for each year
scaler = StandardScaler()
results = {}

for year in range(1971, 2022):
    year_data = data[data['Year'] == str(year)]
    features = scaler.fit_transform(year_data[selected_columns[1:]].values)
    som = MiniSom(2, 3, features.shape[1], sigma=0.7, learning_rate=0.1, neighborhood_function='gaussian', random_seed=10)
    som.train_batch(features, 500, verbose=False)
    winner_coordinates = np.array([som.winner(x) for x in features]).T
    cluster_index = np.ravel_multi_index(winner_coordinates, (2, 3))
    results[year] = (features, cluster_index, year_data['Region/Country/Economy'].values)

# Create animation frames and initial data
frames = []
for year, (features, clusters, countries) in results.items():
    frame_data = []
    for cluster_id in np.unique(clusters):
        mask = clusters == cluster_id
        hover_texts = [
            f"{country}<br>" + "<br>".join([f"{col}: {val:.2f}" for col, val in zip(selected_columns[1:], row)])
            for country, row in zip(countries[mask], features[mask])
        ]
        scatter = go.Scatter(
            x=features[mask, 0],
            y=features[mask, 1],
            mode='markers',
            marker=dict(size=12, line=dict(width=2)),
            text=hover_texts,  # Set hover text to the formatted string
            hoverinfo='text',  # Ensure hover displays the text
            name=f'Cluster {cluster_id}',  # Name for the legend
            legendgroup=f'Cluster {cluster_id}',  # Grouping in the legend
            showlegend=True  # Always show the legend
        )
        frame_data.append(scatter)
    frames.append(go.Frame(data=frame_data, name=str(year)))

# Build figure with animation controls
fig = go.Figure(
    data=frames[0].data,  # Initial data from the first frame
    frames=frames,
    layout=go.Layout(
        title="SOM Clusters Visualization by Year",
        updatemenus=[dict(
            type="buttons",
            showactive=True,
            buttons=[dict(label="Play",
                          method="animate",
                          args=[None, {"frame": {"duration": 500, "redraw": True}, "fromcurrent": True, "transition": {"duration": 300}}],
                          ),
                    dict(label="Pause",
                         method="animate",
                         args=[[None], {"frame": {"duration": 0, "redraw": False}, "mode": "immediate", "transition": {"duration": 0}}]),
                    ])],
        sliders=[dict(
            steps=[{"args": [[f.name], {"frame": {"duration": 300, "redraw": True}, "mode": "immediate", "transition": {"duration": 300}}],
                    "label": f.name, "method": "animate"} for f in frames],
            transition={"duration": 300},
            x=0, y=0, len=1.0)],
        xaxis=dict(title='Feature 1 (Scaled)'), yaxis=dict(title='Feature 2 (Scaled)')
    )
)

# Show figure
fig.show()
